In [28]:
import pandas as pd
from urllib import request
import folium
from folium.plugins import TimestampedGeoJson
import json
from geojson import Point, Feature, FeatureCollection, dump
import pickle
from datetime import datetime, date
import os

# Get Data

Data was referred from Data is Plural via email subscription

Data is from [NYC Parks and Recreation - Street Tree Planting Locations](https://www.nycgovparks.org/trees/street-tree-planting/locations)



In [29]:
def get_most_recent_upload_date():
    r = request.urlopen('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv')

    last_build_date = r.readlines()[5].decode('utf-8').split(',')[1].strip('\n')

    last_build_date = datetime.strptime(last_build_date.strip('"'), '%Y-%m-%d %H:%M:%S')

    return last_build_date

In [30]:
def download_new_data():

    df = pd.read_csv('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv', skiprows=7)
    df['CompletedDate'] = pd.to_datetime(df['CompletedDate'])
    df['PlantingSeason'] = pd.to_datetime(df['PlantingSeason'])

    return df

In [31]:
def load_tree_data(save=True, return_data=True):

    today = datetime.now()
    file_names = os.listdir('../data/')
    today_file = f'../data/street_tree_planting_{today.strftime("%Y_%m_%d")}.pkl'

    if os.path.exists(today_file):
        df = pd.read_pickle(today_file)

    elif not os.path.exists(today_file):
        most_recent_web = get_most_recent_upload_date()
        if most_recent_web < today:
            most_recent_file = f'../data/street_tree_planting_{most_recent_web.strftime("%Y_%m_%d")}.pkl'
            if os.path.exists(most_recent_file):
                df = pd.read_pickle(most_recent_file)
            elif not os.path.exists(most_recent_file):
                df = download_new_data()
                if save:
                    df.to_pickle(f'../data/street_tree_planting_{most_recent_web.strftime("%Y_%m_%d")}.pkl')
        elif most_recent_web == today:
            df = get_most_recent_upload_date()
            if save:
                df.to_pickle(today_file)

    if return_data:
        return df


In [32]:
df = load_tree_data()
df

lng        lat    Borough  ZipCode BuildingNumber  \
0    -73.709503  40.740340     Queens    11004         82-030   
1    -73.954008  40.814634  Manhattan    10027            464   
2    -73.712984  40.735428     Queens    11001         254-04   
3    -73.952187  40.799678  Manhattan    10026             37   
4    -73.876284  40.828165      Bronx    10472           1155   
...         ...        ...        ...      ...            ...   
8180 -73.785172  40.727778     Queens    11366         183-02   
8181 -73.810892  40.777863     Queens    11357         151-41   
8182 -73.708925  40.743219     Queens    11004          81-04   
8183 -73.870720  40.896687      Bronx    10470            143   
8184 -73.903583  40.854817      Bronx    10453            110   

                   StreetName  FiscalYear  PlantingSpaceID  CommunityBoard  \
0                  260 STREET           0           148027             413   
1             WEST 129 STREET           0           156427             109   
2                     84 ROAD           0           177638             413   
3         MALCOLM X BOULEVARD           0           178031             110   
4                MANOR AVENUE           0           191641             209   
...                       ...         ...              ...             ...   
8180           UNION TURNPIKE           0          4309386             408   
8181  WILLETS POINT BOULEVARD           0          4995347             407   
8182               262 STREET           0          4302751             413   
8183          EAST 233 STREET           0          5803374             212   
8184          EAST 181 STREET           0           432549             205   

     PlantingSeason  CityCouncil    TreeID      WOId       WOStatus  \
0        2022-05-31           23    114029  15525248      Completed   
1        2022-05-31            7         0  16644663  Not Completed   
2        2022-05-31           23    142438   8573730      Completed   
3        2022-05-31            9    143233   9138879  Not Completed   
4        2022-05-31           18         0  14343624  Not Completed   
...             ...          ...       ...       ...            ...   
8180     2022-05-31           24  13133256  12931606      Completed   
8181     2022-05-31           19  13133260  14373476      Completed   
8182     2022-05-31           23  13133270  16743002      Completed   
8183     2022-05-31           11  13133286  15866418      Completed   
8184     2022-05-31           14  13134156  13213090      Completed   

     CompletedDate  
0       2021-12-07  
1              NaT  
2       2021-12-07  
3              NaT  
4              NaT  
...            ...  
8180    2022-05-24  
8181    2022-05-09  
8182    2022-04-21  
8183    2022-06-28  
8184    2022-06-10  

[8185 rows x 15 columns]

In [27]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)
nyc_map

In [7]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)
records = df[df['WOStatus'] == 'Completed'][['lat', 'lng', 'CompletedDate']].to_records()

for record in records:
    folium.Marker(location=[record[1], record[2]],
                  icon=folium.Icon(color='green',
                                   icon_color='white',
                                   icon='tree',
                                   prefix='fa',
                                   ),
                  # popup=record[4],
                  tooltip=f"Completed Date: {record[3]}"
                  ).add_to(nyc_map)

nyc_map

In [33]:
def df_to_geojson(df, properties, lat='latitude', lon='longitude'):
    # create a new python dict to contain our geojson data, using geojson format
    geojson = {'type':'FeatureCollection', 'features':[]}

    # loop through each row in the dataframe and convert each row to geojson format
    for _, row in df.iterrows():
        # create a feature template to fill in
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}

        # fill in the coordinates
        feature['geometry']['coordinates'] = [row[lon],row[lat]]

        # for each column, get the value and add it as a new feature property
        for prop in properties:
            feature['properties'][prop] = row[prop]

        # add this feature (aka, converted dataframe row) to the list of features inside our dict
        geojson['features'].append(feature)

    return geojson

In [34]:
df_for_geojson = df[df['WOStatus'] == 'Completed'].rename({'lat': 'latitude', 'lng': 'longitude', 'CompletedDate': 'times'}, axis=1)
df_for_geojson['times'] = df_for_geojson['times'].astype(str)

geojson = df_to_geojson(df=df_for_geojson, properties=['times'], lat='latitude', lon='longitude')

In [35]:
with open('dataset.geojson', 'w') as f:
    dump(geojson, f)

In [36]:
with open('dataset.geojson') as j:
    data = json.load(j)

In [37]:
for i in range(len(data['features'])):
    data['features'][i]['properties']['times'] = [data['features'][i]['properties']['times'][:19]]

In [38]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)

TimestampedGeoJson(data, transition_time=2).add_to(nyc_map)
nyc_map